In [10]:
import torch
from terrain_nerfacto.utils.siren import Siren
import plotly.graph_objects as go

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

Load model

In [8]:
heightnet = Siren(in_features=2, out_features=1, hidden_features=256, hidden_layers=3, outermost_linear=True)
heightnet.load_state_dict(torch.load('red_rocks_height_net.pth'))
heightnet.to(device)
pass

Generate grid of xy points

In [4]:
N = 256
x, y = torch.meshgrid(
    torch.linspace(-2, 2, N, requires_grad=True, device=device),
    torch.linspace(-2, 2, N, requires_grad=True, device=device),
    indexing='ij'
)
XY_grid = torch.stack((x, y), dim=-1)
positions = XY_grid.reshape(-1, 2)

In [9]:
with torch.no_grad():
    height, coords = heightnet(positions)

height = height.reshape(N, N).cpu().numpy()

In [14]:
fig = go.Figure(data=[go.Surface(z=height, x=x.detach().cpu().numpy(), y=y.detach().cpu().numpy())])
fig.update_layout(width=1200, height=600)
fig.show()

In [19]:
positions.shape

torch.Size([65536, 2])

Compute heights and plot heatmap

In [20]:
heights = pipeline.model.field.positions_to_heights(positions)

In [21]:
def gradient(y, x, grad_outputs=None):
    if grad_outputs is None:
        grad_outputs = torch.ones_like(y)
    grad = torch.autograd.grad(y, [x], grad_outputs=grad_outputs, create_graph=True)[0]
    return grad

In [22]:
h_x = gradient(heights, x)
h_y = gradient(heights, y)

In [23]:
torch.max(h_x)

tensor(62.9042, device='cuda:0', grad_fn=<MaxBackward1>)

In [ ]:
heights = pipeline.model.field.positions_to_heights(positions)

# Remove outliers



fig = px.imshow(heights.reshape(N, N).detach().cpu().numpy())

# fig = px.imshow(gradient(heights, x).detach().cpu().numpy())
fig.show()